step1.
quick computing in edge,provide reliability
step2.
feature importance distributing,providing reliability
step3.
traditional data --> compression --> ML --> Acc
BE data(by feature importance) --> compression --> ML --> Acc

In [268]:
import jupyter_Importer
from MLModels_FeatureImportance import featureImportance_linearRegression
from MLModels_FeatureImportance import featureImportance_permutation
from MLModels_FeatureImportance import featureImportance_DTree

import pandas as pd
import numpy as np
import math
from sklearn import preprocessing
from sklearn.cluster import KMeans
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import train_test_split


In [269]:
dataset = pd.read_csv("Occupancy.csv", names = ['x' + str(i) for i in range(1, 7)] + ['y'], sep = ",")
dataset.head()

x1           x2        x3                x4  \
0                 date  Temperature  Humidity             Light   
1  2015-02-02 14:19:00         23.7    26.272             585.2   
2  2015-02-02 14:19:59       23.718     26.29             578.4   
3  2015-02-02 14:21:00        23.73     26.23  572.666666666667   
4  2015-02-02 14:22:00      23.7225    26.125            493.75   

                 x5                  x6          y  
0               CO2       HumidityRatio  Occupancy  
1             749.2  0.0047641630241641          1  
2             760.4  0.0047726609921251          1  
3  769.666666666667  0.0047651525524654          1  
4            774.75  0.0047437733559968          1

In [270]:
#pick light,co2,y
dataset_light_co2 = dataset.iloc[1:,3:5]
dataset_light_co2['y'] = dataset.iloc[1:,6:7]
dataset_light_co2.columns = ['x1','x2','y']
dataset_light_co2['x1'] = dataset_light_co2['x1'].apply(lambda x : float(x))
dataset_light_co2['x2'] = dataset_light_co2['x2'].apply(lambda x : float(x))
dataset_light_co2['y'] = dataset_light_co2['y'].apply(lambda x : int(x))
dataset_light_co2

x1           x2  y
1      585.200000   749.200000  1
2      578.400000   760.400000  1
3      572.666667   769.666667  1
4      493.750000   774.750000  1
5      488.600000   779.000000  1
...           ...          ... ..
20556  429.750000  1505.250000  1
20557  423.500000  1514.500000  1
20558  423.500000  1521.500000  1
20559  418.750000  1632.000000  1
20560  409.000000  1864.000000  1

[20560 rows x 3 columns]

In [271]:
minmax = preprocessing.MinMaxScaler()
dataset_light_co2 = minmax.fit_transform(dataset_light_co2)
dataset_light_co2 = pd.DataFrame(dataset_light_co2)
dataset_light_co2.columns = ['x1','x2','y']
dataset_light_co2

x1        x2    y
0      0.344793  0.202224  1.0
1      0.340787  0.208956  1.0
2      0.337409  0.214525  1.0
3      0.290912  0.217581  1.0
4      0.287877  0.220135  1.0
...         ...       ...  ...
20555  0.253204  0.656649  1.0
20556  0.249521  0.662209  1.0
20557  0.249521  0.666416  1.0
20558  0.246723  0.732832  1.0
20559  0.240978  0.872276  1.0

[20560 rows x 3 columns]

In [272]:
subset = dataset_light_co2.sample(frac=0.2,replace=False,random_state=43)
dataset_light_co2 = dataset_light_co2.append(subset)
dataset_light_co2 = dataset_light_co2.drop_duplicates(subset=['x1','x2','y'],keep=False)

subsample_x = subset.iloc[:,:-1].values
subsample_y = subset.iloc[:,-1].values

#using in Eculidean dist
error_a = []
error_b = []
for i in range(0,21) :
    error_a.append(i)
    error_b.append(20-i)

#using in cosine dist
error_a_cos = []
error_b_cos = []
for i in range(0,25):
    error_a_cos.append(i)
    error_b_cos.append(25-i)

print(error_a,error_b)
print(dataset_light_co2.info(),subset.info())

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20] [20, 19, 18, 17, 16, 15, 14, 13, 12, 11, 10, 9, 8, 7, 6, 5, 4, 3, 2, 1, 0]
<class 'pandas.core.frame.DataFrame'>
Int64Index: 6757 entries, 0 to 20559
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   x1      6757 non-null   float64
 1   x2      6757 non-null   float64
 2   y       6757 non-null   float64
dtypes: float64(3)
memory usage: 211.2 KB
<class 'pandas.core.frame.DataFrame'>
Int64Index: 4112 entries, 8854 to 4673
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   x1      4112 non-null   float64
 1   x2      4112 non-null   float64
 2   y       4112 non-null   float64
dtypes: float64(3)
memory usage: 128.5 KB
None None


In [273]:
importanceReg,RegCoef = featureImportance_linearRegression(subsample_x,subsample_y)
model = KNeighborsClassifier(n_neighbors=5,algorithm="brute")  
model.fit(subsample_x,subsample_y)  
importancePermu,PermuCoef = featureImportance_permutation(model,subsample_x,subsample_y)
importanceDTree,DTreeCoef = featureImportance_DTree(subsample_x,subsample_y)
print("RegCoef : " +str(RegCoef))
print("importanceReg : "+str(importanceReg))
print("PermuCoef : "+str(PermuCoef))
print("importancePermu : "+str(importancePermu))
print("DTreeCoef : " +str(DTreeCoef))
print("importanceDTree : "+str(importanceDTree))

RegCoef : [2.910980313625912, 0.256307040639797]
importanceReg : [0.919076796017702, 0.08092320398229802]
PermuCoef : [0.29756809338521406, 0.058803501945525305]
importancePermu : [0.834993858332196, 0.16500614166780403]
DTreeCoef : [0.9597756771798792, 0.04022432282012079]
importanceDTree : [0.9597756771798792, 0.04022432282012079]


In [274]:
#BE for bounded err
#iter for iteration or not
#neg for negative importance or not
#importance for two feature importance ratio
#df for dataframe
#dist 1 for Eculidean dist,2 for cosine dist

def df_2feature_be_generates(BE,iter=1,neg=0,importance=importanceReg,df=dataset_light_co2,dist=1):
    temp = df.copy()
    df_2feature_be = pd.DataFrame.to_numpy(dataset_light_co2)
    e1 = 0
    e2 = 0

    if dist == 1 :#Eculidean distance
        if iter == 1 and neg == 0:
            e1 = temp['x1'].mean()*BE*(error_a[iter]/(error_a[iter]+error_b[iter]))
            e2 = temp['x2'].mean()*BE*(error_b[iter]/(error_a[iter]+error_b[iter]))
        elif iter == 0 and neg == 1:
            e1 = temp['x1'].mean()*BE*importance[0]
            e2 = temp['x2'].mean()*BE*importance[1]
        elif iter == 0 and neg == 0:
            e1 = temp['x1'].mean()*BE*importance[1]
            e2 = temp['x2'].mean()*BE*importance[0]
        
        for idx,cell in temp['x1'].iteritems():
            temp['x1'][idx] += e1
        temp = temp.to_numpy()
        df_2feature_be = np.vstack((df_2feature_be,temp))
        temp = dataset_light_co2.copy()

        for idx,cell in temp['x1'].iteritems():
            temp['x1'][idx] = temp['x1'][idx] - e1
        temp = temp.to_numpy()
        df_2feature_be = np.vstack((df_2feature_be,temp))
        temp = dataset_light_co2.copy()

        for idx,cell in temp['x2'].iteritems():
            temp['x2'][idx] += e2
        temp = temp.to_numpy()
        df_2feature_be = np.vstack((df_2feature_be,temp))
        temp = dataset_light_co2.copy()

        for idx,cell in temp['x2'].iteritems():
            temp['x2'][idx] = temp['x2'][idx] - e2
        temp = temp.to_numpy()
        df_2feature_be = np.vstack((df_2feature_be,temp))
        temp = dataset_light_co2.copy()

        df_2feature_be = pd.DataFrame(df_2feature_be)
        
    elif dist == 2 :#cosine dist
        
        if iter == 1 and neg == 0:
            e1 = temp['x1'].mean()*BE*math.cos((error_a_cos[iter]/(error_a_cos[iter]+error_b_cos[iter])))
            e2 = temp['x2'].mean()*BE*math.sin((error_b_cos[iter]/(error_a_cos[iter]+error_b_cos[iter])))
        elif iter == 0 and neg == 1:
            e1 = temp['x1'].mean()*BE*importance[0]
            e2 = temp['x2'].mean()*BE*importance[1]
        elif iter == 0 and neg == 0:
            e1 = temp['x1'].mean()*BE*importance[1]
            e2 = temp['x2'].mean()*BE*importance[0]

        for idx,cell in temp['x1'].iteritems():
            temp['x1'][idx] += e1
        temp = temp.to_numpy()
        df_2feature_be = np.vstack((df_2feature_be,temp))
        temp = dataset_light_co2.copy()

        for idx,cell in temp['x2'].iteritems():
            temp['x2'][idx] += e2
        temp = temp.to_numpy()
        df_2feature_be = np.vstack((df_2feature_be,temp))
        temp = dataset_light_co2.copy()
        df_2feature_be = pd.DataFrame(df_2feature_be)
    return df_2feature_be


eculidean dist

In [275]:
#using importanceReg as error allocation rate to predict by svm
BE = 0.2
df_2feature_be = df_2feature_be_generates(BE,-1,0,importanceReg)
x_be = df_2feature_be.iloc[:, :-1].values
y_be = df_2feature_be.iloc[:,-1].values
X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
clf_BE_SVC_importanceReg = SVC(kernel='linear',C=1,gamma='auto')
clf_BE_SVC_importanceReg.fit(X_train, y_train)
y_BE_importanceReg_svm_predict = clf_BE_SVC_importanceReg.predict(X_test)
result_BE_train = clf_BE_SVC_importanceReg.score(X_train, y_train)
result_BE_test = clf_BE_SVC_importanceReg.score(X_test, y_test)
subset_raw = clf_BE_SVC_importanceReg.score(subsample_x, subsample_y)
print('BESVM Accuracy (on training) = with x1 bounded error ('+str(BE)+'%*'+str(importanceReg[1])+'),x2 with error ('+str(BE)+'%*'+str(importanceReg[0])+') : '+str(result_BE_train))
print('BESVM Accuracy (on testing) = with x1 bounded error ('+str(BE)+'%*'+str(importanceReg[1])+'),x2 with error ('+str(BE)+'%*'+str(importanceReg[0])+') : '+str(result_BE_test))
print('BESVM Accuracy (on subset_raw) = with no bounded error,x2 with no error '+str(subset_raw))


BESVM Accuracy (on training) = with x1 bounded error (0.2%*0.08092320398229802),x2 with error (0.2%*0.919076796017702) : 0.9734719550096197
BESVM Accuracy (on testing) = with x1 bounded error (0.2%*0.08092320398229802),x2 with error (0.2%*0.919076796017702) : 0.9743969217108184
BESVM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.9878404669260701


In [276]:
#using importancePermu as error allocation rate to predict by svm
df_2feature_be = df_2feature_be_generates(BE,-1,0,importancePermu)
x_be = df_2feature_be.iloc[:, :-1].values
y_be = df_2feature_be.iloc[:,-1].values
X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
clf_BE_SVC_importancePermu = SVC(kernel='linear',C=1,gamma='auto')
clf_BE_SVC_importancePermu.fit(X_train, y_train)
y_BE_importancePermu_svm_predict = clf_BE_SVC_importancePermu.predict(X_test)
result_BE_train = clf_BE_SVC_importancePermu.score(X_train, y_train)
result_BE_test = clf_BE_SVC_importancePermu.score(X_test, y_test)
subset_raw = clf_BE_SVC_importancePermu.score(subsample_x, subsample_y)
print('BESVM Accuracy (on training) = with x1 bounded error ('+str(BE)+'%*'+str(importancePermu[1])+'),x2 with error ('+str(BE)+'%*'+str(importancePermu[0])+') : '+str(result_BE_train))
print('BESVM Accuracy (on testing) = with x1 bounded error ('+str(BE)+'%*'+str(importancePermu[1])+'),x2 with error ('+str(BE)+'%*'+str(importancePermu[0])+') : '+str(result_BE_test))
print('BESVM Accuracy (on subset_raw) = with no bounded error,x2 with no error '+str(subset_raw))



BESVM Accuracy (on training) = with x1 bounded error (0.2%*0.16500614166780403),x2 with error (0.2%*0.834993858332196) : 0.9734719550096197
BESVM Accuracy (on testing) = with x1 bounded error (0.2%*0.16500614166780403),x2 with error (0.2%*0.834993858332196) : 0.9743969217108184
BESVM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.9878404669260701


In [277]:
#using importanceDTree as error allocation rate to predict by svm
df_2feature_be = df_2feature_be_generates(BE,-1,0,importanceDTree)
x_be = df_2feature_be.iloc[:, :-1].values
y_be = df_2feature_be.iloc[:,-1].values
X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
clf_BE_SVC_importanceDTree = SVC(kernel='linear',C=1,gamma='auto')
clf_BE_SVC_importanceDTree.fit(X_train, y_train)
y_BE_importanceDTree_svm_predict = clf_BE_SVC_importanceDTree.predict(X_test)
result_BE_train = clf_BE_SVC_importanceDTree.score(X_train, y_train)
result_BE_test = clf_BE_SVC_importanceDTree.score(X_test, y_test)
subset_raw = clf_BE_SVC_importanceDTree.score(subsample_x, subsample_y)
print('BESVM Accuracy (on training) = with x1 bounded error ('+str(BE)+'%*'+str(importanceDTree[1])+'),x2 with error ('+str(BE)+'%*'+str(importanceDTree[0])+') : '+str(result_BE_train))
print('BESVM Accuracy (on testing) = with x1 bounded error ('+str(BE)+'%*'+str(importanceDTree[1])+'),x2 with error ('+str(BE)+'%*'+str(importanceDTree[0])+') : '+str(result_BE_test))
print('BESVM Accuracy (on subset_raw) = with no bounded error,x2 with no error '+str(subset_raw))



BESVM Accuracy (on training) = with x1 bounded error (0.2%*0.04022432282012079),x2 with error (0.2%*0.9597756771798792) : 0.9734719550096197
BESVM Accuracy (on testing) = with x1 bounded error (0.2%*0.04022432282012079),x2 with error (0.2%*0.9597756771798792) : 0.9743969217108184
BESVM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.9878404669260701


(20%*0.5,20*0.5) could be viewed as initial err distribution

In [278]:
#brute force allocation
#brute force from 0-20 using svm
BE = 0.2
for i in range(21) :
    df_2feature_be = df_2feature_be_generates(BE,i,0)
    x_be = df_2feature_be.iloc[:, :-1].values
    y_be = df_2feature_be.iloc[:,-1].values
    X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
    clf_BE = SVC(kernel='linear',C=1,gamma='auto')
    clf_BE.fit(X_train, y_train)
    y_BE_predict = clf_BE.predict(X_test)
    result_BE_train = clf_BE.score(X_train, y_train)
    result_BE_test = clf_BE.score(X_test, y_test)
    subset_raw = clf_BE.score(subsample_x, subsample_y)
    print('BESVM Accuracy (on training) = with x1 bounded error ('+str(BE)+'%*'+str((error_a[i]/(error_a[i]+error_b[i])))+'),x2 with error ('+str(BE)+'%*'+str((error_b[i]/(error_a[i]+error_b[i])))+') : '+str(result_BE_train))
    print('BESVM Accuracy (on testing) = with x1 bounded error ('+str(BE)+'%*'+str((error_a[i]/(error_a[i]+error_b[i])))+'),x2 with error ('+str(BE)+'%*'+str((error_b[i]/(error_a[i]+error_b[i])))+') : '+str(result_BE_test))
    print('BESVM Accuracy (on subset_raw) = with no bounded error,x2 with no error '+str(subset_raw))
    

BESVM Accuracy (on training) = with x1 bounded error (0.2%*0.0),x2 with error (0.2%*1.0) : 0.9735089536776677
BESVM Accuracy (on testing) = with x1 bounded error (0.2%*0.0),x2 with error (0.2%*1.0) : 0.973952937694243
BESVM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.9878404669260701
BESVM Accuracy (on training) = with x1 bounded error (0.2%*0.05),x2 with error (0.2%*0.95) : 0.9736199496818114
BESVM Accuracy (on testing) = with x1 bounded error (0.2%*0.05),x2 with error (0.2%*0.95) : 0.973952937694243
BESVM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.9878404669260701
BESVM Accuracy (on training) = with x1 bounded error (0.2%*0.1),x2 with error (0.2%*0.9) : 0.9734719550096197
BESVM Accuracy (on testing) = with x1 bounded error (0.2%*0.1),x2 with error (0.2%*0.9) : 0.9743969217108184
BESVM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.9878404669260701
BESVM Accuracy (on training) = with x1 bounded error (0.2%*0.15),x2 

In [279]:
#using importanceReg as error allocation rate to predict by knn
df_2feature_be = df_2feature_be_generates(BE,-1,0,importanceReg)
x_be = df_2feature_be.iloc[:, :-1].values
y_be = df_2feature_be.iloc[:,-1].values
X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
KNN_BE_importanceReg = KNeighborsClassifier()
KNN_BE_importanceReg.fit(X_train, y_train)
y_BE_importanceReg_knn_predict = KNN_BE_importanceReg.predict(X_test)
result_BE_train = KNN_BE_importanceReg.score(X_train, y_train)
result_BE_test = KNN_BE_importanceReg.score(X_test, y_test)
subset_raw = KNN_BE_importanceReg.score(subsample_x, subsample_y)
print('BEKNN Accuracy (on training) = with x1 bounded error ('+str(BE)+'%*'+str(importanceReg[1])+'),x2 with error ('+str(BE)+'%*'+str(importanceReg[0])+') : '+str(result_BE_train))
print('BEKNN Accuracy (on testing) = with x1 bounded error ('+str(BE)+'%*'+str(importanceReg[1])+'),x2 with error ('+str(BE)+'%*'+str(importanceReg[0])+') : '+str(result_BE_test))
print('BEKNN Accuracy (on subset_raw) = with no bounded error,x2 with no error '+str(subset_raw))


BEKNN Accuracy (on training) = with x1 bounded error (0.2%*0.08092320398229802),x2 with error (0.2%*0.919076796017702) : 0.9991490306348971
BEKNN Accuracy (on testing) = with x1 bounded error (0.2%*0.08092320398229802),x2 with error (0.2%*0.919076796017702) : 0.9945241971289034
BEKNN Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.982976653696498


In [280]:
#using importancePermu as error allocation rate to predict by knn
df_2feature_be = df_2feature_be_generates(BE,-1,0,importancePermu)
x_be = df_2feature_be.iloc[:, :-1].values
y_be = df_2feature_be.iloc[:,-1].values
X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
KNN_BE_importancePermu = KNeighborsClassifier()
KNN_BE_importancePermu.fit(X_train, y_train)
y_BE_importancePermu_knn_predict = KNN_BE_importancePermu.predict(X_test)
result_BE_train = KNN_BE_importancePermu.score(X_train, y_train)
result_BE_test = KNN_BE_importancePermu.score(X_test, y_test)
subset_raw = KNN_BE_importancePermu.score(subsample_x, subsample_y)
print('BEKNN Accuracy (on training) = with x1 bounded error ('+str(BE)+'%*'+str(importancePermu[1])+'),x2 with error ('+str(BE)+'%*'+str(importancePermu[0])+') : '+str(result_BE_train))
print('BEKNN Accuracy (on testing) = with x1 bounded error ('+str(BE)+'%*'+str(importancePermu[1])+'),x2 with error ('+str(BE)+'%*'+str(importancePermu[0])+') : '+str(result_BE_test))
print('BEKNN Accuracy (on subset_raw) = with no bounded error,x2 with no error '+str(subset_raw))


BEKNN Accuracy (on training) = with x1 bounded error (0.2%*0.16500614166780403),x2 with error (0.2%*0.834993858332196) : 0.9991490306348971
BEKNN Accuracy (on testing) = with x1 bounded error (0.2%*0.16500614166780403),x2 with error (0.2%*0.834993858332196) : 0.9945241971289034
BEKNN Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.982976653696498


In [281]:
#using importanceDTree as error allocation rate to predict by knn
df_2feature_be = df_2feature_be_generates(BE,-1,0,importanceDTree)
x_be = df_2feature_be.iloc[:, :-1].values
y_be = df_2feature_be.iloc[:,-1].values
X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
KNN_BE_importanceDTree = KNeighborsClassifier()
KNN_BE_importanceDTree.fit(X_train, y_train)
y_BE_importanceDTree_knn_predict = KNN_BE_importanceDTree.predict(X_test)
result_BE_train = KNN_BE_importanceDTree.score(X_train, y_train)
result_BE_test = KNN_BE_importanceDTree.score(X_test, y_test)
subset_raw = KNN_BE_importanceDTree.score(subsample_x, subsample_y)
print('BEKNN Accuracy (on training) = with x1 bounded error ('+str(BE)+'%*'+str(importanceDTree[1])+'),x2 with error ('+str(BE)+'%*'+str(importanceDTree[0])+') : '+str(result_BE_train))
print('BEKNN Accuracy (on testing) = with x1 bounded error ('+str(BE)+'%*'+str(importanceDTree[1])+'),x2 with error ('+str(BE)+'%*'+str(importanceDTree[0])+') : '+str(result_BE_test))
print('BEKNN Accuracy (on subset_raw) = with no bounded error,x2 with no error '+str(subset_raw))


BEKNN Accuracy (on training) = with x1 bounded error (0.2%*0.04022432282012079),x2 with error (0.2%*0.9597756771798792) : 0.9991490306348971
BEKNN Accuracy (on testing) = with x1 bounded error (0.2%*0.04022432282012079),x2 with error (0.2%*0.9597756771798792) : 0.9945241971289034
BEKNN Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.982976653696498


In [282]:
#using knn with brute force from 0-20
for i in range(21):
    df_2feature_be = df_2feature_be_generates(BE,i,0)
    x_be = df_2feature_be.iloc[:, :-1].values
    y_be = df_2feature_be.iloc[:,-1].values
    X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
    KNN_BE = KNeighborsClassifier()
    KNN_BE.fit(X_train,y_train)
    y_BE_predict = KNN_BE.predict(X_test)
    result_BE_train = KNN_BE.score(X_train, y_train)
    result_BE_test = KNN_BE.score(X_test, y_test)
    subset_raw = KNN_BE.score(subsample_x, subsample_y)
    
    print('BEKNN Accuracy (on training) = with x1 bounded error ('+str(BE)+'%*'+str((error_a[i]/(error_a[i]+error_b[i])))+'),x2 with error ('+str(BE)+'%*'+str((error_b[i]/(error_a[i]+error_b[i])))+') : '+str(result_BE_train))
    print('BEKNN Accuracy (on testing) = with x1 bounded error ('+str(BE)+'%*'+str((error_a[i]/(error_a[i]+error_b[i])))+'),x2 with error ('+str(BE)+'%*'+str((error_b[i]/(error_a[i]+error_b[i])))+') : '+str(result_BE_test))
    print('BEKNN Accuracy (on subset_raw) = with no bounded error,x2 with no error '+str(subset_raw))
    

BEKNN Accuracy (on training) = with x1 bounded error (0.2%*0.0),x2 with error (0.2%*1.0) : 0.9798357259138671
BEKNN Accuracy (on testing) = with x1 bounded error (0.2%*0.0),x2 with error (0.2%*1.0) : 0.9748409057273938
BEKNN Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.9878404669260701
BEKNN Accuracy (on training) = with x1 bounded error (0.2%*0.05),x2 with error (0.2%*0.95) : 0.9815746633121207
BEKNN Accuracy (on testing) = with x1 bounded error (0.2%*0.05),x2 with error (0.2%*0.95) : 0.9745449163830102
BEKNN Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.9885700389105059
BEKNN Accuracy (on training) = with x1 bounded error (0.2%*0.1),x2 with error (0.2%*0.9) : 0.9991490306348971
BEKNN Accuracy (on testing) = with x1 bounded error (0.2%*0.1),x2 with error (0.2%*0.9) : 0.9945241971289034
BEKNN Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.982976653696498
BEKNN Accuracy (on training) = with x1 bounded error (0.2%*0.15),x2

In [283]:
#importanceReg,KMeans
df_2feature_be = df_2feature_be_generates(BE,-1,0,importanceReg)
x_be = df_2feature_be.iloc[:, :-1].values
#x_be = preprocessing.scale(x_be)#標準化
y_be = df_2feature_be.iloc[:,-1].values
X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
KM_BE_importanceReg=KMeans(n_clusters=1,init='random',random_state=5)
KM_BE_importanceReg.fit(X_train)
y_BE_importanceReg_KMeans_predict = KM_BE_importanceReg.predict(X_train)
y_BE_predict_test = KM_BE_importanceReg.predict(X_test)
#subsample_x = preprocessing.scale(subsample_x)
y_subset = KM_BE_importanceReg.predict(subsample_x)
result_BE_train = 1 - np.sum(y_BE_predict!=y_train)/len(y_train)
result_BE_test = 1 - np.sum(y_BE_predict_test!=y_train)/len(y_test)
subset_raw = 1 - np.sum(subsample_y!=y_subset)/len(subsample_y)
    
    
print('BEKM Accuracy (on training) = with x1 bounded error ('+str(BE)+'%*'+str(importanceReg[1])+'),x2 with error ('+str(BE)+'%*'+str(importanceReg[0])+') : '+str(result_BE_train))
print('BEKM Accuracy (on testing) = with x1 bounded error ('+str(BE)+'%*'+str(importanceReg[1])+'),x2 with error ('+str(BE)+'%*'+str(importanceReg[0])+') : '+str(result_BE_test))
print('BEKM Accuracy (on subset_raw) = with no bounded error,x2 with no error '+str(subset_raw))

BEKM Accuracy (on training) = with x1 bounded error (0.2%*0.08092320398229802),x2 with error (0.2%*0.919076796017702) : 0.999963001331952
BEKM Accuracy (on testing) = with x1 bounded error (0.2%*0.08092320398229802),x2 with error (0.2%*0.919076796017702) : 0.9998520053278082
BEKM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.7665369649805447


d:\BESVM\BESVM\.venv\lib\site-packages\ipykernel_launcher.py:13: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  del sys.path[0]
d:\BESVM\BESVM\.venv\lib\site-packages\ipykernel_launcher.py:14: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  


In [284]:
#importancePermu,KMeans
df_2feature_be = df_2feature_be_generates(BE,-1,0,importancePermu)
x_be = df_2feature_be.iloc[:, :-1].values
#x_be = preprocessing.scale(x_be)#標準化
y_be = df_2feature_be.iloc[:,-1].values
X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
KM_BE_importancePermu=KMeans(n_clusters=1,init='random',random_state=5)
KM_BE_importancePermu.fit(X_train)
y_BE_importancePermu_KMeans__predict = KM_BE_importancePermu.predict(X_train)
y_BE_predict_test = KM_BE_importancePermu.predict(X_test)
subsample_x = preprocessing.scale(subsample_x)
y_subset = KM_BE_importancePermu.predict(subsample_x)
result_BE_train = 1 - np.sum(y_BE_predict!=y_train)/len(y_train)
result_BE_test = 1 - np.sum(y_BE_predict_test!=y_train)/len(y_test)
subset_raw = 1 - np.sum(subsample_y!=y_subset)/len(subsample_y)
    
    
print('BEKM Accuracy (on training) = with x1 bounded error ('+str(BE)+'%*'+str(importancePermu[1])+'),x2 with error ('+str(BE)+'%*'+str(importancePermu[0])+') : '+str(result_BE_train))
print('BEKM Accuracy (on testing) = with x1 bounded error ('+str(BE)+'%*'+str(importancePermu[1])+'),x2 with error ('+str(BE)+'%*'+str(importancePermu[0])+') : '+str(result_BE_test))
print('BEKM Accuracy (on subset_raw) = with no bounded error,x2 with no error '+str(subset_raw))

BEKM Accuracy (on training) = with x1 bounded error (0.2%*0.16500614166780403),x2 with error (0.2%*0.834993858332196) : 0.999963001331952
BEKM Accuracy (on testing) = with x1 bounded error (0.2%*0.16500614166780403),x2 with error (0.2%*0.834993858332196) : 0.9998520053278082
BEKM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.7665369649805447


d:\BESVM\BESVM\.venv\lib\site-packages\ipykernel_launcher.py:13: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  del sys.path[0]
d:\BESVM\BESVM\.venv\lib\site-packages\ipykernel_launcher.py:14: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  


In [285]:
#importanceDTree,KMeans
df_2feature_be = df_2feature_be_generates(BE,-1,0,importanceDTree)
x_be = df_2feature_be.iloc[:, :-1].values
#x_be = preprocessing.scale(x_be)#標準化
y_be = df_2feature_be.iloc[:,-1].values
X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
KM_BE_importanceDTree=KMeans(n_clusters=1,init='random',random_state=5)
KM_BE_importanceDTree.fit(X_train)
y_BE_importanceDTree_KMeans_predict = KM_BE_importanceDTree.predict(X_train)
y_BE_predict_test = KM_BE_importanceDTree.predict(X_test)
#subsample_x = preprocessing.scale(subsample_x)
y_subset = KM_BE_importanceDTree.predict(subsample_x)
result_BE_train = 1 - np.sum(y_BE_predict!=y_train)/len(y_train)
result_BE_test = 1 - np.sum(y_BE_predict_test!=y_train)/len(y_test)
subset_raw = 1 - np.sum(subsample_y!=y_subset)/len(subsample_y)
    
    
print('BEKM Accuracy (on training) = with x1 bounded error ('+str(BE)+'%*'+str(importanceDTree[1])+'),x2 with error ('+str(BE)+'%*'+str(importanceDTree[0])+') : '+str(result_BE_train))
print('BEKM Accuracy (on testing) = with x1 bounded error ('+str(BE)+'%*'+str(importanceDTree[1])+'),x2 with error ('+str(BE)+'%*'+str(importanceDTree[0])+') : '+str(result_BE_test))
print('BEKM Accuracy (on subset_raw) = with no bounded error,x2 with no error '+str(subset_raw))

BEKM Accuracy (on training) = with x1 bounded error (0.2%*0.04022432282012079),x2 with error (0.2%*0.9597756771798792) : 0.999963001331952
BEKM Accuracy (on testing) = with x1 bounded error (0.2%*0.04022432282012079),x2 with error (0.2%*0.9597756771798792) : 0.9998520053278082
BEKM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.7665369649805447


d:\BESVM\BESVM\.venv\lib\site-packages\ipykernel_launcher.py:13: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  del sys.path[0]
d:\BESVM\BESVM\.venv\lib\site-packages\ipykernel_launcher.py:14: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  


In [286]:
#using kMeans with brute force from 0-20
for i in range(21):
    df_2feature_be = df_2feature_be_generates(BE,i,0)
    x_be = df_2feature_be.iloc[:, :-1].values
    #x_be = preprocessing.scale(x_be)#標準化
    y_be = df_2feature_be.iloc[:,-1].values
    X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
    KM_BE=KMeans(n_clusters=1,init='random',random_state=5)
    KM_BE.fit(X_train)
    y_BE_predict = KM_BE.predict(X_train)
    y_BE_predict_test = KM_BE.predict(X_test)
    subsample_x = preprocessing.scale(subsample_x)
    y_subset = KM_BE.predict(subsample_x)
    result_BE_train = 1 - np.sum(y_BE_predict!=y_train)/len(y_train)
    #print(score)
    result_BE_test = 1 - np.sum(y_BE_predict_test!=y_train)/len(y_test)
    subset_raw = 1 - np.sum(subsample_y!=y_subset)/len(subsample_y)
    #print(score)
    #result_BE_train = KM_BE.score(X_train, y_train)
    #result_BE_test = KM_BE.score(X_test, y_test)
    #subset_raw = KM_BE.score(subsample_x, subsample_y)
    
    
    print('BEKM Accuracy (on training) = with x1 bounded error ('+str(BE)+'%*'+str((error_a[i]/(error_a[i]+error_b[i])))+'),x2 with error ('+str(BE)+'%*'+str((error_b[i]/(error_a[i]+error_b[i])))+') : '+str(result_BE_train))
    print('BEKM Accuracy (on testing) = with x1 bounded error ('+str(BE)+'%*'+str((error_a[i]/(error_a[i]+error_b[i])))+'),x2 with error ('+str(BE)+'%*'+str((error_b[i]/(error_a[i]+error_b[i])))+') : '+str(result_BE_test))
    print('BEKM Accuracy (on subset_raw) = with no bounded error,x2 with no error '+str(subset_raw))
    

d:\BESVM\BESVM\.venv\lib\site-packages\ipykernel_launcher.py:16: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  


BEKM Accuracy (on training) = with x1 bounded error (0.2%*0.0),x2 with error (0.2%*1.0) : 0.4710670415865029
BEKM Accuracy (on testing) = with x1 bounded error (0.2%*0.0),x2 with error (0.2%*1.0) : 0.9998520053278082
BEKM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.7665369649805447


d:\BESVM\BESVM\.venv\lib\site-packages\ipykernel_launcher.py:16: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  


BEKM Accuracy (on training) = with x1 bounded error (0.2%*0.05),x2 with error (0.2%*0.95) : 0.4710670415865029
BEKM Accuracy (on testing) = with x1 bounded error (0.2%*0.05),x2 with error (0.2%*0.95) : 0.9998520053278082
BEKM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.7665369649805447


d:\BESVM\BESVM\.venv\lib\site-packages\ipykernel_launcher.py:16: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  


...

d:\BESVM\BESVM\.venv\lib\site-packages\ipykernel_launcher.py:16: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  


BEKM Accuracy (on training) = with x1 bounded error (0.2%*0.9),x2 with error (0.2%*0.1) : 0.4710670415865029
BEKM Accuracy (on testing) = with x1 bounded error (0.2%*0.9),x2 with error (0.2%*0.1) : 0.9998520053278082
BEKM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.7665369649805447


d:\BESVM\BESVM\.venv\lib\site-packages\ipykernel_launcher.py:16: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  


BEKM Accuracy (on training) = with x1 bounded error (0.2%*0.95),x2 with error (0.2%*0.05) : 0.4710670415865029
BEKM Accuracy (on testing) = with x1 bounded error (0.2%*0.95),x2 with error (0.2%*0.05) : 0.9998520053278082
BEKM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.7665369649805447
BEKM Accuracy (on training) = with x1 bounded error (0.2%*1.0),x2 with error (0.2%*0.0) : 0.4710670415865029
BEKM Accuracy (on testing) = with x1 bounded error (0.2%*1.0),x2 with error (0.2%*0.0) : 0.9998520053278082
BEKM Accuracy (on subset_raw) = with no bounded error,x2 with no error 0.7665369649805447


d:\BESVM\BESVM\.venv\lib\site-packages\ipykernel_launcher.py:16: DeprecationWarning: elementwise comparison failed; this will raise an error in the future.
  


implement the ML trust model,test ML models which is trained above

In [300]:
#take err distribution 20%*0.5,20%*0.5 as ML model in edge and train knn
importanceEdge = [0.5,0.5]
#using importanceEdge as error allocation rate to predict by svm,KNN,Kmeans
BE = 0.2
df_2feature_be = df_2feature_be_generates(BE,-1,0,importanceEdge)
x_be = df_2feature_be.iloc[:, :-1].values
y_be = df_2feature_be.iloc[:,-1].values
X_train,X_test,y_train, y_test = train_test_split(x_be, y_be, test_size=0.2,random_state=1)
clf_BE_SVC_importanceEdge = SVC(kernel='linear',C=1,gamma='auto')
KNN_BE_importanceEdge = KNeighborsClassifier()
KM_BE_importanceEdge = KMeans(n_clusters=1,init='random',random_state=5)

clf_BE_SVC_importanceEdge.fit(X_train, y_train)
KNN_BE_importanceEdge.fit(X_train,y_train)
KM_BE_importanceEdge.fit(X_train)

y_BE_importanceEdge_svm_predict = clf_BE_SVC_importanceEdge.predict(X_test)
y_BE_importanceEdge_knn_predict = KNN_BE_importanceEdge.predict(X_test)
y_BE_importanceEdge_KM_predict = KM_BE_importanceEdge.predict(X_test)

result_BE_train = clf_BE_SVC_importanceEdge.score(X_train, y_train)
result_BE_test = clf_BE_SVC_importanceEdge.score(X_test, y_test)

print(X_test.shape,y_BE_importanceEdge_svm_predict.shape)
print(X_train.shape)

## preprocess data for knn from ml models
KNN_Xtest_predictY = pd.DataFrame(X_test)
y = pd.DataFrame(y_BE_importanceEdge_svm_predict)
KNN_Xtest_predictY['y'] = y
KNN_Xtest_predictY.columns = ['x1','x2','y']
print(KNN_Xtest_predictY.info())       

(6757, 2) (6757,)
(27028, 2)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6757 entries, 0 to 6756
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   x1      6757 non-null   float64
 1   x2      6757 non-null   float64
 2   y       6757 non-null   float64
dtypes: float64(3)
memory usage: 158.5 KB
None


In [301]:
X_fitKNN = KNN_Xtest_predictY.iloc[:,:-1]
y_fitKNN = KNN_Xtest_predictY.iloc[:,-1]
KNN_trust_importanceEdge = KNeighborsClassifier(n_neighbors=3,weights='uniform',algorithm='brute',p=2)

X_fitKNN = np.array(X_fitKNN)
y_fitKNN = np.array(y_fitKNN)

KNN_trust_importanceEdge.fit(X_fitKNN,y_fitKNN)

# x is used for ML training above are here as predict data for KNN
y_KNN_trust_predict =  KNN_trust_importanceEdge.predict(X_train)
print(np.size(y_KNN_trust_predict),np.size(y_train))

27028 27028


In [302]:
#trust computing data preprocessing
data_trust_KNN = pd.DataFrame(X_train)
data_trust_KNN['y'] = y_KNN_trust_predict
data_trust_KNN.columns = ['x1','x2','y']

data_trust = pd.DataFrame(X_train)
data_trust['y'] = y_train
data_trust.columns = ['x1','x2','y']

print(data_trust_KNN.info(),data_trust.info())
#print(data_trust_KNN)
print(data_trust) 

## trust computing




<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27028 entries, 0 to 27027
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   x1      27028 non-null  float64
 1   x2      27028 non-null  float64
 2   y       27028 non-null  float64
dtypes: float64(3)
memory usage: 633.6 KB
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27028 entries, 0 to 27027
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   x1      27028 non-null  float64
 1   x2      27028 non-null  float64
 2   y       27028 non-null  float64
dtypes: float64(3)
memory usage: 633.6 KB
None None
             x1        x2    y
0      0.094270  0.166041  1.0
1      0.273383  0.451841  1.0
2      0.215938  0.130428  1.0
3      0.267492  0.320661  1.0
4      0.000000  0.029842  0.0
...         ...       ...  ...
27023  0.266902  0.184373  0.0
27024  0.000000  0.224543  0.0
27025  0.182648  0.132081  1.0
27026  0.0

In [303]:
y_train = np.array(y_train)
index = np.arange(0,27028)
equal = []
diff = []
for i in range(len(y_train)):
    if y_train[i] == y_KNN_trust_predict[i]:
        equal.append(i)
    else:
        diff.append(i)

print(len(diff))

12143


In [304]:
dist = KNN_trust_importanceEdge.kneighbors(X_train,n_neighbors=3)
dist

(array([[0.00569549, 0.00659161, 0.01347347],
        [0.00015026, 0.00150263, 0.0031078 ],
        [0.00435155, 0.00435155, 0.00747784],
        ...,
        [0.00137384, 0.00170298, 0.00203664],
        [0.        , 0.        , 0.00020035],
        [0.00064112, 0.00110193, 0.0012021 ]]),
 array([[ 607,  706, 4467],
        [3302, 6507, 3254],
        [ 667, 5916, 1014],
        ...,
        [2236,  690, 2576],
        [1284, 1626, 3207],
        [3760, 2752,  680]], dtype=int64))

In [305]:
def trustComputing(train_x,train_y,predict_y,dist):
    sum = 0
    for i in range(len(predict_y)):
        if train_y[i] == predict_y[i]:
            if predict_y[i] == 0:
                ## cal
                temp_0=[]
                sum_0=0 ##here
                for j in range(3):
                    if train_y[dist[1][i][j]] == 0:
                        temp_0.append(dist[0][i][j])
                        sum_0+=dist[0][i][j]
                sum = sum+(1/(sum_0/((len(temp_0)+1))+1))
                print(1/(sum_0/((len(temp_0)+1))+1))
                print("test2")
                temp_0.clear()
            else :
                ## cal
                temp_1=[]
                sum_1=0 ##here
                for j in range(3):
                    if train_y[dist[1][i][j]] == 1:
                        temp_1.append(dist[0][i][j])
                        sum_1+=dist[0][i][j]
                sum = sum+(1/(sum_1/(len(temp_1)+1)+1))
                print(1/(sum_1/(len(temp_1)+1)+1))
                print("test2")
                temp_1.clear()
        else :
            if predict_y[i] == 1:
                temp_1=[]
                temp_0=[]
                temp_1.append(1000)##
                sum_0=0##
                sum_1=0##

                for j in range(3):
                    if train_y[dist[1][i][j]] == 0 :
                        temp_0.append(dist[0][i][j])
                        sum_0+=dist[0][i][j]
                    else:
                        temp_1.append(dist[0][i][j])
                        sum_1+=dist[0][i][j]
                if(len(temp_0)==0):##               
                    print(0)
                else:
                    
                    if min(temp_0) < min(temp_1):
                        sum = sum+(1/(sum_1/2+1))
                        print((1/(sum_1/2+1)))
                    else:
                        sum = sum+(1/(sum_0+1))
                        print((1/(sum_0+1)))
                print("test1")
                temp_0.clear()
                temp_1.clear()
            else :
                temp_1=[]
                temp_0=[]
                temp_0.append(1000)##
                sum_0=0##
                sum_1=0##

                for j in range(3):
                    print(train_y[dist[1][i][j]])
                    if train_y[dist[1][i][j]] == 0:
                        temp_0.append(dist[0][i][j])
                        sum_0+=dist[0][i][j]
                    else:
                        temp_1.append(dist[0][i][j])
                        sum_1+=dist[0][i][j]
                if(len(temp_1)==0):               
                    print(0)
                else:
                    
                    if min(temp_1) < min(temp_0):
                        sum = sum+(1/(sum_0/2+1))
                        print((1/(sum_0/2+1)))
                    else:
                        sum = sum+(1/(sum_1+1))
                        print((1/(sum_1+1)))
                print("test1")
                temp_0.clear()
                temp_1.clear()
    aver = sum/len(train_y)
    return aver

In [306]:
score = trustComputing(X_train,y_train,y_KNN_trust_predict,dist)
print("score = ",score)

0.993601068650684
test2
0.998465547069427
test2
0.9962750059330909
test2
1.0
test2
0.9998798040806514
test1
0.9996995643683455
test2
1.0
test2
1.0
test2
0.9946196383201319
test1
0.9995947991679823
test1
0.9981528287772196
test1
0.9987341027026574
test2
0.9938509251655813
test1
0.9989271684276347
test2
0.9927824940934672
test2
0.9875352426176008
test1
1.0
test1
1.0
test2
0.9997878702736285
test2
0.9925344013754269
test1
0.9979059283466174
test2
1.0
test1
0.9972528545535605
test1
0.9999999925494194
test1
0.9994658850708512
test1
0.9994333106603415
test2
0.9987993396368006
test2
1.0
test2
1.0
test2
0.9929188443518063
test1
0.9995327336748832
test2
0.993539194617516
test2
0.9989992494370754
test2
0.9999999986829109
test2
0.9985974072830911
test2
0.999449339207052
test2
0.9999666093460369
test2
0.9985995098284394
test1
0.9997328698802875
test2
0.9996143282390141
test2
0.9989687689886083
test1
0.9998831424660365
test2
0.9965578404183584
test1
0.9991992392773167
test1
0.9992992642274381
test2

check the accuracy in edge ml
trust computing in step2 (after be ml)
inflate the no error data do ml vs BE distributed data with ml

In [307]:
#combine raw data x and the predicted y by BE model
dataset_light_co2_BEML_y = dataset_light_co2
dataset_light_co2_BEML_y['y'] = y_BE_importanceReg_svm_predict
# train knn
X_fitKNN = dataset_light_co2_BEML_y.iloc[:,:-1]
y_fitKNN = dataset_light_co2_BEML_y.iloc[:,-1]
X_fitKNN = np.array(X_fitKNN)
y_fitKNN = np.array(y_fitKNN)
KNN_trust_BEML = KNeighborsClassifier(n_neighbors=3,weights='uniform',algorithm='brute',p=2)
KNN_trust_subsample = KNeighborsClassifier(n_neighbors=3,weights='uniform',algorithm='brute',p=2)
KNN_trust_BEML.fit(X_fitKNN,y_fitKNN)
KNN_trust_subsample.fit(subsample_x,subsample_y)

KNeighborsClassifier(algorithm='brute', n_neighbors=3)

In [308]:
#
y_BEML_KNN_trust_predict = KNN_trust_BEML.predict(subsample_x)
print(np.size(y_BEML_KNN_trust_predict),np.size(subsample_y))

4112 4112


In [309]:
#dist = KNN_trust_BEML.kneighbors(subsample_x,n_neighbors=3)
dist = KNN_trust_subsample.kneighbors(subsample_x,n_neighbors=3)
dist

(array([[0.        , 0.        , 0.00052701],
        [0.        , 0.00158103, 0.01106718],
        [0.        , 0.        , 0.        ],
        ...,
        [0.        , 0.        , 0.        ],
        [0.        , 0.00474308, 0.0091976 ],
        [0.        , 0.        , 0.        ]]),
 array([[   0, 3371, 1035],
        [   1, 3652, 2307],
        [   2,  558, 2578],
        ...,
        [ 484,  553,  856],
        [4110, 3139, 3824],
        [ 198,  239,  284]], dtype=int64))

In [310]:
print(np.size(dist),np.max(dist))

24672 4110.0


In [311]:
score_importanceReg_svm = trustComputing(subsample_x,subsample_y,y_BEML_KNN_trust_predict,dist)
print("score = ",score_importanceReg_svm)

1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
1.0
1.0
1.0
test1
0.9871082589120611
test2
1.0
1.0
1.0
1.0
test1
1.0
test1
1.0
test1
1.0
test1
0.9941263183878504
test2
0.9849196817954844
test2
1.0
test1
1.0
test1
0.9767461807416514
test2
1.0
test1
1.0
test1
1.0
test1
0.9875100134164093
test1
1.0
test2
1.0
test1
0.9966515708506449
test2
1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
test1
0.9999341282845312
test2
0.9858290414829816
test2
0.9753277150627159
test2
1.0
test1
1.0
1.0
1.0
1.0
test1
1.0
test1
1.0
test1
1.0
test1
0.9750583199464067
test2
0.9896909306654657
test2
1.0
1.0
1.0
1.0
test1
1.0
test1
1.0
test1
1.0
1.0
1.0
1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
1.0
1.0
1.0
test1
1.0
test1
1.0
test1
1.0
test1
0.9988156353960721
test2
1.0
test1
0.995409842863665
test2
1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
test1
1.0
test1
0.998128667592507
test2
0.9943278840014756
test2
1.0
test1
0.9837309347618634
test2


In [312]:
KNN_Xtest_predictY = pd.DataFrame(X_test)
y = pd.DataFrame(y_BE_importanceEdge_knn_predict)
KNN_Xtest_predictY['y'] = y
KNN_Xtest_predictY.columns = ['x1','x2','y']

X_fitKNN = KNN_Xtest_predictY.iloc[:,:-1]
y_fitKNN = KNN_Xtest_predictY.iloc[:,-1]
KNN_trust_importanceEdge = KNeighborsClassifier(n_neighbors=3,weights='uniform',algorithm='brute',p=2)

X_fitKNN = np.array(X_fitKNN)
y_fitKNN = np.array(y_fitKNN)

KNN_trust_importanceEdge.fit(X_fitKNN,y_fitKNN)

# x is used for ML training above are here as predict data for KNN
y_KNN_trust_predict =  KNN_trust_importanceEdge.predict(X_train)
print(np.size(y_KNN_trust_predict),np.size(y_train))

dist = KNN_trust_importanceEdge.kneighbors(X_train,n_neighbors=3)
score = trustComputing(X_train,y_train,y_KNN_trust_predict,dist)
print("score = ",score)



27028 27028
0.993601068650684
test2
0.998465547069427
test2
0.9962750059330909
test2
1.0
test2
1.0
test2
1.0
0.0
1.0
0.9990992343492308
test1
1.0
test2
1.0
1.0
0.0
1.0
test1
0.9946196383201319
test1
0.9997298271387156
test2
0.9990755605896717
test2
0.9987341027026574
test2
0.9938509251655813
test1
0.9989271684276347
test2
1.0
0.0
0.0
0.9856684264040135
test1
0.9875352426176008
test1
1.0
test1
1.0
test2
0.9997878702736285
test2
0.9962532146900854
test2
0.0
1.0
1.0
0.9937439861225005
test1
1.0
test1
0.9992049808652088
test2
0.9999999962747097
test2
0.9994658850708512
test1
0.9994333106603415
test2
1.0
1.0
1.0
1.0
test1
1.0
test2
1.0
test2
0.9964468419432819
test2
0.0
1.0
1.0
0.9985995098284411
test1
1.0
0.0
1.0
0.9950914426063929
test1
0.9989992494370754
test2
1.0
0.0
0.0
0.9963591799936545
test1
1.0
0.0
1.0
0.9987782317670105
test1
1.0
1.0
1.0
1.0
test1
1.0
0.0
1.0
0.9999499148552434
test1
0.9992992642274385
test2
0.9997328698802875
test2
0.9996143282390141
test2
0.9994841184978024
test

In [313]:
KNN_Xtest_predictY = pd.DataFrame(X_test)
y = pd.DataFrame(y_BE_importanceEdge_KM_predict)
KNN_Xtest_predictY['y'] = y
KNN_Xtest_predictY.columns = ['x1','x2','y']

X_fitKNN = KNN_Xtest_predictY.iloc[:,:-1]
y_fitKNN = KNN_Xtest_predictY.iloc[:,-1]
KNN_trust_importanceEdge = KNeighborsClassifier(n_neighbors=3,weights='uniform',algorithm='brute',p=2)

X_fitKNN = np.array(X_fitKNN)
y_fitKNN = np.array(y_fitKNN)

KNN_trust_importanceEdge.fit(X_fitKNN,y_fitKNN)

# x is used for ML training above are here as predict data for KNN
y_KNN_trust_predict =  KNN_trust_importanceEdge.predict(X_train)
print(np.size(y_KNN_trust_predict),np.size(y_train))

dist = KNN_trust_importanceEdge.kneighbors(X_train,n_neighbors=3)
score = trustComputing(X_train,y_train,y_KNN_trust_predict,dist)
print("score = ",score)



27028 27028
1.0
1.0
1.0
1.0
test1
0.0
1.0
1.0
0.9954107252604276
test1
0.0
0.0
1.0
0.9925776600385009
test1
0.0
0.0
0.0
0
test1
1.0
test2
1.0
0.0
1.0
0.9990992343492308
test1
0.0
0.0
0.0
0
test1
1.0
1.0
0.0
1.0
test1
0.9982000899955005
test2
0.9997298271387156
test2
0.9990755605896717
test2
1.0
0.0
1.0
0.9981023722454636
test1
0.9979418713303881
test2
1.0
1.0
1.0
1.0
test1
1.0
0.0
0.0
0.9856684264040135
test1
0.9937285351650003
test2
1.0
test2
0.0
1.0
0.0
1.0
test1
1.0
0.0
1.0
0.9996818391561291
test1
0.9962532146900854
test2
0.0
1.0
1.0
0.9937439861225005
test1
0.9990867653185392
test2
0.9992049808652088
test2
0.9999999962747097
test2
0.9997328711966849
test2
1.0
0.0
1.0
0.9983018566205248
test1
1.0
1.0
1.0
1.0
test1
0.0
1.0
0.0
1.0
test1
1.0
0.0
0.0
0.9989992494370386
test1
0.9964468419432819
test2
0.0
1.0
1.0
0.9985995098284411
test1
1.0
0.0
1.0
0.9950914426063929
test1
0.0
1.0
1.0
0.997003745318345
test1
1.0
0.0
0.0
0.9963591799936545
test1
1.0
0.0
1.0
0.9987782317670105
test1
1.0
